1. mon_standard.pkl > array code



In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import pickle

USE_SUBLABEL = False
URL_PER_SITE = 10
TOTAL_URLS   = 950

# Load the pickle file
print("Loading datafile...")
with open("/content/drive/MyDrive/Colab Notebooks/2023_2_ML/mon_standard.pkl", 'rb') as fi: # Path to mon_standard.pkl in Colab
    data = pickle.load(fi)


Loading datafile...


In [21]:
X1 = [] # Array to store instances (timestamps) - 19,000 instances, e.g., [[0.0, 0.5, 3.4, ...], [0.0, 4.5, ...], [0.0, 1.5, ...], ... [... ,45.8]]
X2 = [] # Array to store instances (direction*size) - size information
y = [] # Array to store the site of each instance - 19,000 instances, e.g., [0, 0, 0, 0, 0, 0, ..., 94, 94, 94, 94, 94]

# Differentiate instances and sites, and store them in the respective x and y arrays
# x array (direction*timestamp), y array (site label)
for i in range(TOTAL_URLS):
    if USE_SUBLABEL:
        label = i
    else:
        label = i // URL_PER_SITE # Calculate which site's URL the current URL being processed belongs to and set that value as the label. Thus, URLs fetched from the same site are labeled identically.
    for sample in data[i]:
        size_seq = []
        time_seq = []
        for c in sample:
            dr = 1 if c > 0 else -1
            time_seq.append(abs(c))
            size_seq.append(dr) # * 512 생략 (계산의 편의성)
        X1.append(time_seq)
        X2.append(size_seq)


# 1. Data analysis

There are 19000 people, and every 200 people visited the same website.<br>
For example, 0th ~ 199th people visited the website 0, and 200th ~ 399th people visited the website 1, and so on.

- number of classes: 95
- number of samples per class: 200
- total number of samples: 19000

In [ ]:
import csv
import numpy as np

In [ ]:
# 정답 데이터 만들기
y_mon = ['Label']
for i in range(95):
  for _ in range(200):
    y_mon.append(i)

print(y_mon)

['Label', 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 

In [ ]:
# csv 파일 만들고 저장
y_mon_data = [y_mon]
csv_file_mon = '/content/drive/MyDrive/Colab Notebooks/2023_2_ML/mon.csv'

with open(csv_file_mon, mode='w', newline='') as file:
   writer = csv.writer(file)
   writer.writerows(y_mon_data)

# 2. Feature Extraction

### Number of packets

In [22]:
import numpy as np

total_pkt_per_user = ['total_pkt_per_user'] # total number of packets per user (both directions)
total_outgoing_pkt_per_user = ['total_outgoing_pkt_per_user'] # total number of outgoing packets per user
total_incoming_pkt_per_user = ['total_incoming_pkt_per_user'] # total number of incoming packets per use


for i in range(19000): # 각 채널마다
  total_pkt_per_user.append(len(X2[i]))
  total_outgoing_pkt_per_user.append(X2[i].count(1))
  total_incoming_pkt_per_user.append(X2[i].count(-1))

print(total_pkt_per_user)
print(total_outgoing_pkt_per_user)
print(total_incoming_pkt_per_user)

['total_pkt_per_user', 1421, 518, 1358, 1446, 1406, 559, 1376, 1403, 564, 564, 1423, 567, 563, 1443, 1452, 552, 564, 1417, 560, 1178, 629, 5072, 5021, 5221, 1036, 1019, 5183, 1028, 4895, 4950, 5051, 4961, 787, 1016, 5113, 5101, 4948, 1034, 5092, 5028, 4675, 5570, 4696, 4715, 4780, 5723, 4672, 4701, 4743, 4766, 4686, 5545, 4786, 4733, 4296, 5030, 5283, 4978, 4650, 1268, 2230, 2228, 2227, 2219, 2233, 2261, 2245, 1128, 2304, 2253, 2168, 2403, 2316, 2257, 2229, 2366, 2216, 2242, 2242, 2201, 5760, 5657, 5663, 5405, 5649, 7268, 5571, 5803, 3984, 3618, 7522, 5573, 7432, 5640, 7540, 7741, 7457, 5523, 5623, 7892, 9900, 9810, 9840, 9798, 9775, 9813, 4387, 9485, 9755, 9904, 9769, 9864, 2621, 9785, 9771, 9809, 9777, 9767, 9841, 9788, 2499, 1775, 2748, 755, 1953, 2158, 1917, 1978, 2367, 2105, 1886, 1862, 2049, 1888, 2447, 2098, 2095, 1877, 691, 696, 9962, 9961, 9964, 9962, 9962, 9963, 9964, 9963, 9963, 9941, 9963, 9963, 9963, 9964, 9963, 9964, 9962, 9962, 9967, 5556, 1805, 1843, 1902, 1842, 1890, 1

In [ ]:
# CSV 파일에 데이터 추가
with open(csv_file_mon, mode='a', newline='') as file:
    writer = csv.writer(file)
    writer.writerow(total_pkt_per_user)
    writer.writerow(total_outgoing_pkt_per_user)
    writer.writerow(total_incoming_pkt_per_user)

### Number of outgoing/incoming packets as a fraction of the total number of packets

In [ ]:
outgoing_pkt_frac_per_user = ['outgoing_pkt_frac_per_user']  # number of outgoing packets as a fraction of the total number of packets
incoming_pkt_frac_per_user = ['incoming_pkt_frac_per_user']  # number of incoming packets as a fraction of the total number of packets

for i in range(1,19001):
    outgoing_fraction = total_outgoing_pkt_per_user[i] / total_pkt_per_user[i]
    incoming_fraction = total_incoming_pkt_per_user[i] / total_pkt_per_user[i]

    # 값을 소수점 네 번째 자리까지 반올림하여 저장
    outgoing_pkt_frac_per_user.append(round(outgoing_fraction, 4))
    incoming_pkt_frac_per_user.append(round(incoming_fraction, 4))

print(outgoing_pkt_frac_per_user)
print(incoming_pkt_frac_per_user)

IndexError: ignored

In [ ]:
# CSV 파일에 데이터 추가
with open(csv_file_mon, mode='a', newline='') as file:
    writer = csv.writer(file)
    writer.writerow(outgoing_pkt_frac_per_user)
    writer.writerow(incoming_pkt_frac_per_user)

### the total number of incoming/outgoing packets in the first 30 packets.

In [ ]:
outgoing30_per_user = ['outgoing30_per_user'] # number of outgoing packets
incoming30_per_user = ['incoming30_per_user'] # number of incoming packets

for i in range(19000):
  cntOutgoing30 = 0
  cntIncoming30 = 0

  for j in range(30):
    if X2[i][j] == -1:
      cntOutgoing30 += 1
    else:
      cntIncoming30 += 1

  outgoing30_per_user.append(cntOutgoing30)
  incoming30_per_user.append(cntIncoming30)

print(outgoing30_per_user)
print(incoming30_per_user)

['outgoing30_per_user', 21, 22, 23, 21, 22, 22, 23, 22, 22, 22, 22, 22, 22, 22, 22, 22, 23, 23, 22, 22, 21, 20, 21, 21, 21, 21, 21, 20, 21, 21, 21, 20, 21, 22, 22, 21, 20, 20, 21, 20, 22, 22, 22, 22, 23, 22, 22, 22, 23, 21, 21, 22, 22, 22, 23, 22, 22, 21, 22, 22, 22, 22, 22, 22, 21, 22, 22, 21, 23, 21, 22, 22, 22, 22, 22, 22, 22, 22, 22, 23, 22, 21, 21, 22, 23, 22, 23, 23, 23, 22, 21, 22, 23, 22, 22, 22, 22, 22, 22, 22, 21, 22, 22, 22, 22, 22, 22, 23, 22, 24, 22, 22, 23, 21, 22, 23, 22, 22, 22, 22, 22, 22, 23, 22, 22, 22, 23, 21, 22, 22, 22, 22, 21, 21, 22, 23, 23, 22, 22, 22, 23, 22, 22, 22, 21, 22, 23, 23, 22, 21, 22, 22, 21, 21, 22, 22, 22, 22, 24, 22, 22, 22, 23, 21, 22, 23, 23, 22, 23, 22, 23, 22, 22, 22, 22, 21, 23, 21, 21, 22, 22, 22, 21, 21, 22, 22, 23, 22, 22, 22, 22, 22, 23, 23, 21, 22, 22, 21, 22, 22, 18, 19, 18, 18, 18, 18, 18, 18, 18, 19, 18, 18, 18, 18, 18, 18, 19, 18, 19, 18, 22, 21, 22, 22, 21, 22, 21, 20, 22, 22, 22, 21, 22, 22, 21, 21, 21, 22, 21, 20, 19, 18, 18, 19, 

In [ ]:
# CSV 파일에 데이터 추가
with open(csv_file_mon, mode='a', newline='') as file:
    writer = csv.writer(file)
    writer.writerow(outgoing30_per_user)
    writer.writerow(incoming30_per_user)

### The sequence of bursts

In [ ]:
# the sequence of bursts
import numpy as np
bursts = [[] for i in range(19000)]

avg_total_burst_per_user = ['avg_total_burst_per_user']
std_total_burst_per_user = ['std_total_burst_per_user']
#min_total_burst_per_user = []
max_total_burst_per_user = ['max_total_burst_per_user']

avg_incoming_burst_per_user = ['avg_incoming_burst_per_user']
std_incoming_burst_per_user = ['std_incoming_burst_per_user']
min_incoming_burst_per_user = ['min_incoming_burst_per_user']
#max_incoming_burst_per_user = []

avg_outgoing_burst_per_user = ['avg_outgoing_burst_per_user']
std_outgoing_burst_per_user = ['std_outgoing_burst_per_user']
#min_outgoing_burst_per_user = []
max_outgoing_burst_per_user = ['max_outgoing_burst_per_user']

for i in range(19000):
  index = 0
  size = X2[i][0] # 1 or -1

  total_burst = []
  incoming_burst = []
  outgoing_burst = []

  for j in range(1, len(X2[i])):
    if X2[i][j-1] != X2[i][j]: # direction change
      total_burst.append((j-index))
      if(size > 0) :
        outgoing_burst.append(j-index)
      else :
        incoming_burst.append(index-j)
      index = j
      size = X2[i][j]

  if(i==0):
    print(f"total_burst: {total_burst}")
    print(f"outgoing_burst: {outgoing_burst}")
    print(f"incoming_burst: {incoming_burst}")

  total_burst_np = np.array(total_burst)
  incoming_burst_np = np.array(incoming_burst)
  outgoing_burst_np = np.array(outgoing_burst)

  avg_total = np.mean(total_burst)
  std_total = np.std(total_burst)
#  min_total = np.min(total_burst)
  max_total = np.max(total_burst)

  avg_incoming = np.mean(incoming_burst)
  std_incoming = np.std(incoming_burst)
  min_incoming = np.min(incoming_burst)
# max_incoming = np.max(incoming_burst)

  avg_outgoing = np.mean(outgoing_burst)
  std_outgoing = np.std(outgoing_burst)
 # min_outgoing = np.min(outgoing_burst)
  max_outgoing = np.max(outgoing_burst)


  avg_total_burst_per_user.append(round(avg_total,4))
  std_total_burst_per_user.append(round(std_total,4))
# min_total_burst_per_user.append(min_total)
  max_total_burst_per_user.append(max_total)

  avg_incoming_burst_per_user.append(round(avg_incoming,4))
  std_incoming_burst_per_user.append(round(std_incoming,4))
  min_incoming_burst_per_user.append(min_incoming)
# max_incoming_burst_per_user.append(max_incoming)

  avg_outgoing_burst_per_user.append(round(avg_outgoing,4))
  std_outgoing_burst_per_user.append(round(std_outgoing,4))
 # min_outgoing_burst_per_user.append(min_outgoing)
  max_outgoing_burst_per_user.append(max_outgoing)

# [-1, -1, 1, -1, 1, -1, 1, 1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, -1, 1, -1, 1, -1, -1, 1, 1, 1]

total_burst: [2, 1, 1, 1, 1, 2, 14, 1, 1, 1, 2, 3, 1, 1, 3, 2, 1, 2, 9, 1, 2, 1, 1, 1, 66, 1, 2, 1, 10, 8, 1, 2, 12, 1, 50, 1, 21, 4, 9, 1, 60, 1, 8, 1, 4, 1, 28, 1, 36, 1, 36, 1, 28, 1, 22, 1, 50, 1, 28, 1, 22, 1, 50, 1, 10, 1, 18, 1, 31, 1, 50, 1, 16, 1, 3, 1, 40, 1, 22, 1, 38, 2, 50, 1, 43, 3, 1, 1, 3, 2, 5, 1, 10, 1, 40, 1, 39, 1, 11, 1, 19, 1, 2, 6, 1, 1, 4, 3, 9, 1, 50, 1, 15, 1, 35, 1, 11, 4, 1, 3, 9, 2, 7, 1, 6, 2, 15, 1, 17, 1, 15, 1, 32, 2, 1, 2, 14, 2, 1, 1, 4, 2, 1, 2, 10, 1, 2, 2, 1, 1, 3, 2, 3, 2, 1]
outgoing_burst: [1, 1, 2, 1, 1, 3, 1, 2, 2, 1, 1, 1, 1, 1, 8, 2, 1, 1, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 3, 1, 2, 1, 1, 1, 1, 1, 1, 6, 1, 3, 1, 1, 1, 1, 4, 3, 2, 1, 2, 1, 1, 1, 2, 2, 2, 1, 2, 2, 1, 2, 1, 2, 2]
incoming_burst: [-2, -1, -1, -14, -1, -2, -1, -3, -1, -9, -2, -1, -66, -2, -10, -1, -12, -50, -21, -9, -60, -8, -4, -28, -36, -36, -28, -22, -50, -28, -22, -50, -10, -18, -31, -50, -16, -3, -40, -22, -38, -50, -43, -1, -3, -5, -10, 

In [ ]:
print(avg_total_burst_per_user)
print(std_total_burst_per_user)
#print(min_total_burst_per_user)
print(max_total_burst_per_user)

print(avg_incoming_burst_per_user)
print(std_incoming_burst_per_user)
## print(max_incoming_burst_per_user)
print(min_incoming_burst_per_user)

print(avg_outgoing_burst_per_user)
print(std_outgoing_burst_per_user)
## print(min_outgoing_burst_per_user)
print(max_outgoing_burst_per_user)

['avg_total_burst_per_user', 9.1548, 5.5484, 8.9801, 9.0881, 8.949, 6.8765, 8.9869, 9.2781, 6.4598, 6.6118, 9.5369, 6.4943, 6.6, 9.0629, 8.5858, 6.7901, 6.1758, 9.3709, 6.4253, 8.8496, 7.2791, 13.52, 12.4566, 13.2799, 7.4388, 7.4234, 12.3088, 7.7143, 12.1439, 12.466, 13.4667, 13.1538, 7.9394, 7.4088, 14.0412, 14.0831, 12.6496, 8.0078, 12.8212, 12.5589, 10.6469, 11.7738, 10.9953, 11.4696, 10.9862, 11.1977, 11.095, 11.2686, 11.7376, 11.0557, 10.8426, 11.6226, 11.4748, 10.3545, 10.0585, 10.7666, 10.6278, 11.5991, 10.9388, 9.3162, 10.7633, 11.7778, 10.6459, 11.3692, 10.7826, 12.3443, 12.1243, 9.8509, 11.5678, 11.0887, 12.6725, 9.8, 10.5708, 11.2189, 11.5389, 11.2038, 11.3538, 11.8519, 12.1081, 10.8374, 11.1806, 11.614, 10.5832, 11.2349, 11.7912, 12.5077, 10.6095, 11.0937, 11.5449, 11.5176, 12.0336, 11.3947, 11.7024, 10.9283, 11.0705, 11.6391, 11.8162, 10.7223, 11.0, 11.6215, 14.1574, 14.3153, 14.073, 14.3803, 14.059, 14.8411, 11.0404, 14.3915, 13.9914, 14.246, 14.2599, 14.312, 11.1783, 13.

In [ ]:
with open(csv_file_mon, mode='a', newline='') as file:
    writer = csv.writer(file)
    writer.writerow(avg_total_burst_per_user)
    writer.writerow(std_total_burst_per_user)
    writer.writerow(max_total_burst_per_user)
    writer.writerow(avg_incoming_burst_per_user)
    writer.writerow(std_incoming_burst_per_user)
    writer.writerow(min_incoming_burst_per_user)
    writer.writerow(avg_outgoing_burst_per_user)
    writer.writerow(std_outgoing_burst_per_user)
    writer.writerow(max_outgoing_burst_per_user)

### Sequence of cumulative packet sizes

In [ ]:
# sequence of cumulative packet sizes

cumulative = [[] for i in range(19000)]

for i in range(19000):
  sum = 0
  for j in range(len(X2[i])):
    sum += X2[i][j]
    cumulative[i].append(sum)

In [ ]:
import numpy as np

avg_cumulative = ['avg_cumulative']
std_cumulative = ['std_cumulative']
min_cumulative = ['min_cumulative']
# max_cumulative = ['max_cumulative']

for arr in cumulative:
    # 각 1차원 배열의 평균, 표준편차, 최소값, 최대값 계산하여 배열에 추가
    avg_cumulative.append(round(np.mean(arr),4))
    std_cumulative.append(round(np.std(arr),4))
    min_cumulative.append(np.min(arr))
    # max_cumulative.append(np.max(arr))

print(avg_cumulative)
print(std_cumulative)
print(min_cumulative)
# print(max_cumulative)

['avg_cumulative', -600.6988, -169.3571, -580.1141, -617.8914, -602.6679, -204.7191, -592.3343, -594.9009, -206.8333, -202.2695, -610.7013, -210.642, -203.8934, -620.596, -618.3264, -200.3659, -205.2482, -609.6789, -204.6107, -501.7071, -188.2273, -1708.1372, -1689.4712, -1747.9389, -330.4633, -328.6143, -1727.1499, -344.43, -1675.8594, -1702.4265, -1748.099, -1694.765, -252.4574, -336.3248, -1777.4866, -1742.337, -1675.8929, -327.2157, -1729.9085, -1669.5712, -1913.9662, -2306.1215, -1935.3803, -1938.1875, -1961.3916, -2371.5992, -1910.7971, -1983.9147, -1965.117, -1958.1748, -1924.4343, -2294.1221, -1983.7035, -1956.0023, -1791.9083, -2094.9903, -2186.3699, -2054.0613, -1925.152, -558.6972, -909.8256, -925.8501, -915.1908, -929.9441, -902.5746, -940.4295, -922.2659, -387.5833, -963.3411, -927.1518, -903.7878, -972.9921, -938.5311, -923.1577, -921.6855, -976.8009, -924.1128, -928.0789, -908.4411, -914.6611, -2421.9615, -2386.7136, -2358.2246, -2283.1317, -2434.6113, -3049.2529, -2373.

In [ ]:
with open(csv_file_mon, mode='a', newline='') as file:
    writer = csv.writer(file)
    writer.writerow(avg_cumulative)
    writer.writerow(std_cumulative)
    writer.writerow(min_cumulative)

In [ ]:
csv_file_mon = '/content/drive/MyDrive/Colab Notebooks/2023_2_ML/mon.csv'

# CSV 파일 열기
with open(csv_file_mon, mode='r') as file:
    reader = csv.reader(file)
    for row in reader:
        first_element = row[0]  # 각 행의 첫 번째 원소
        print(first_element)

Label
total_pkt_per_user
total_outgoing_pkt_per_user
total_incoming_pkt_per_user
outgoing_pkt_frac_per_user
incoming_pkt_frac_per_user
outgoing30_per_user
incoming30_per_user
avg_total_burst_per_user
std_total_burst_per_user
max_total_burst_per_user
avg_incoming_burst_per_user
std_incoming_burst_per_user
min_incoming_burst_per_user
avg_outgoing_burst_per_user
std_outgoing_burst_per_user
max_outgoing_burst_per_user
avg_cumulative
std_cumulative
min_cumulative




```
# 코드로 형식 지정됨
```

### Time interval (both directions, outgoing, incoming)

In [ ]:
# time interval (both directions, outgoing, incoming)
interval = [[] for i in range(19000)]

for i in range(19000):
  for j in range(1, len(X1[i])):
    tmp = X1[i][j] - X1[i][j-1]
    interval[i].append(tmp)

In [ ]:
import numpy as np

avg_interval = ['avg_interval']
std_interval = ['std_interval']
# min_interval = ['min_cumulative']
max_interval = ['max_interval']

for arr in interval:
    # 각 1차원 배열의 평균, 표준편차, 최소값, 최대값 계산하여 배열에 추가
    avg_interval.append(round(np.mean(arr),4))
    std_interval.append(round(np.std(arr),4))
    #min_interval.append(np.min(arr))
    max_interval.append(round(np.max(arr),4))

print(avg_interval)
print(std_interval)
# print(min_interval)
print(max_interval)

['avg_interval', 0.0071, 0.0197, 0.0082, 0.0092, 0.0076, 0.0192, 0.0115, 0.0063, 0.021, 0.0219, 0.009, 0.0216, 0.0254, 0.0074, 0.0075, 0.0213, 0.0186, 0.0075, 0.0414, 0.0244, 0.063, 0.0103, 0.0039, 0.0035, 0.0095, 0.0107, 0.0038, 0.0097, 0.0047, 0.004, 0.0039, 0.0032, 0.0288, 0.0199, 0.0082, 0.0111, 0.0036, 0.0097, 0.004, 0.0111, 0.0017, 0.0032, 0.0028, 0.0015, 0.0018, 0.0031, 0.0016, 0.0025, 0.0036, 0.0018, 0.0017, 0.0016, 0.002, 0.0038, 0.0122, 0.0021, 0.0098, 0.0023, 0.0029, 0.05, 0.0044, 0.005, 0.0051, 0.0053, 0.0079, 0.0044, 0.0049, 0.0506, 0.0056, 0.0048, 0.0054, 0.0046, 0.0061, 0.005, 0.0047, 0.0056, 0.0057, 0.0041, 0.0056, 0.0053, 0.0015, 0.0027, 0.0017, 0.0024, 0.0021, 0.0019, 0.0019, 0.0019, 0.0031, 0.0027, 0.002, 0.0031, 0.0019, 0.0042, 0.0047, 0.0025, 0.0038, 0.0021, 0.0016, 0.0027, 0.0014, 0.0015, 0.0024, 0.0013, 0.0021, 0.0011, 0.013, 0.0057, 0.0014, 0.0018, 0.0015, 0.0012, 0.0202, 0.0056, 0.0013, 0.0012, 0.0017, 0.0014, 0.0012, 0.0013, 0.0136, 0.0213, 0.0207, 0.0296, 0.0

In [ ]:
with open(csv_file_mon, mode='a', newline='') as file:
    writer = csv.writer(file)
    writer.writerow(avg_interval)
    writer.writerow(std_interval)
    writer.writerow(max_interval)

### Number of packets in fixed time

In [ ]:
import numpy as np

#1초 간격
time_interval=1.0
packets_in_fixed_time = [[] for i in range(19000)]

for i in range(19000):
  start_time=X1[i][0]
  end_time=start_time+time_interval
  a=0
  for timestamp in X1[i]:
    if timestamp<=end_time:
      a+=1
    else:
      packets_in_fixed_time[i].append(a)
      a=1
      start_time=end_time
      end_time+=time_interval
  packets_in_fixed_time[i].append(a)

# Calculate stats for each array in packets_in_fixed_time
avg_pkts_in_fixed_time = ['avg_pkts_in_fixed_time']
std_pkts_in_fixed_time = ['std_pkts_in_fixed_time']
min_pkts_in_fixed_time = ['min_pkts_in_fixed_time']
max_pkts_in_fixed_time = ['max_pkts_in_fixed_time']

for arr in packets_in_fixed_time:
    arr = np.array(arr)
    avg_pkts_in_fixed_time.append(round(np.mean(arr),4))
    std_pkts_in_fixed_time.append(round(np.std(arr),4))
    min_pkts_in_fixed_time.append(np.min(arr))
    max_pkts_in_fixed_time.append(np.max(arr))

# Print or use the computed statistics
print(avg_pkts_in_fixed_time)
print(std_pkts_in_fixed_time)
print(min_pkts_in_fixed_time)
print(max_pkts_in_fixed_time)

['avg_pkts_in_fixed_time', 129.1818, 64.75, 123.4545, 103.2857, 127.8182, 62.1111, 86.0, 175.375, 56.4, 51.2727, 109.4615, 51.5455, 43.3077, 131.1818, 132.0, 61.3333, 70.5, 128.8182, 23.3333, 40.6207, 15.725, 253.6, 251.05, 274.7895, 103.6, 92.6364, 259.15, 102.8, 233.0952, 247.5, 252.55, 310.0625, 34.2174, 48.381, 121.7381, 115.9318, 274.8889, 103.4, 242.4762, 139.6667, 584.375, 309.4444, 361.2308, 589.375, 531.1111, 317.9444, 584.0, 391.75, 279.0, 529.5556, 520.6667, 616.1111, 478.6, 262.9444, 97.6364, 457.2727, 114.8478, 414.8333, 332.1429, 105.6667, 278.75, 278.5, 185.5833, 184.9167, 124.0556, 323.0, 249.4444, 19.4483, 209.4545, 250.3333, 180.6667, 218.4545, 154.4, 225.7, 247.6667, 215.0909, 184.6667, 320.2857, 186.8333, 183.4167, 640.0, 353.5625, 566.3, 386.0714, 470.75, 519.1429, 506.4545, 483.5833, 306.4615, 361.8, 470.125, 309.6111, 495.4667, 235.0, 209.4444, 387.05, 257.1379, 460.25, 562.3, 358.7273, 707.1429, 700.7143, 410.0, 890.7273, 465.4762, 892.0909, 76.9649, 172.4545, 6

In [ ]:
with open(csv_file_mon, mode='a', newline='') as file:
    writer = csv.writer(file)
    writer.writerow(avg_pkts_in_fixed_time)
    writer.writerow(std_pkts_in_fixed_time)
    writer.writerow(min_pkts_in_fixed_time)
    writer.writerow(max_pkts_in_fixed_time)

###sum of Intervals of continuous packets

In [ ]:
def sum_interval(X1,X2):
  sum_intervals_continuous = [[] for i in range(19000)]

  for i in range(19000):
    start_pack=X2[i][0]
    start_time=X1[i][0]
    end_time=X1[i][0]

    for j in range(1,len(X1[i])):
      if start_pack == X2[i][j]: #512 or -512
        end_time=X1[i][j]
        continue
      else:
        end_time=X1[i][j]
        sum_intervals_continuous[i].append(round(end_time-start_time,3))
        start_time=end_time
    sum_intervals_continuous[i].append(round(end_time-start_time,3))

  return sum_intervals_continuous

In [ ]:
sum_intervals_continuous=sum_interval(X1,X2)

# 평균, 표준편차, 최소값, 최대값을 저장할 배열 초기화
avg_sum_intervals_continuous = ['avg_sum_intervals_continuous']
std_sum_intervals_continuous = ['std_sum_intervals_continuous']
# min_sum_intervals_continuous = ['min_sum_intervals_continuous']
max_sum_intervals_continuous = ['max_sum_intervals_continuous']

for arr in sum_intervals_continuous:
    # 각 1차원 배열의 평균, 표준편차, 최소값, 최대값 계산하여 배열에 추가
    avg_sum_intervals_continuous.append(round(np.mean(arr),4))
    std_sum_intervals_continuous.append(round(np.std(arr),4))
    #min_sum_intervals_continuous.append(np.min(arr))
    max_sum_intervals_continuous.append(np.max(arr))

print(avg_sum_intervals_continuous)
print(std_sum_intervals_continuous)
#print(min_sum_intervals_continuous)
print(max_sum_intervals_continuous)

['avg_sum_intervals_continuous', 0.0831, 0.1254, 0.0934, 0.1086, 0.0917, 0.1557, 0.1366, 0.0697, 0.1665, 0.1647, 0.1081, 0.1801, 0.1979, 0.0912, 0.0797, 0.1654, 0.1433, 0.0918, 0.3351, 0.2877, 0.3504, 0.0326, 0.0125, 0.0112, 0.0597, 0.0682, 0.0121, 0.0679, 0.0157, 0.0133, 0.0129, 0.0107, 0.1857, 0.1322, 0.0271, 0.0383, 0.0121, 0.059, 0.013, 0.0356, 0.0182, 0.0397, 0.0289, 0.0166, 0.0202, 0.0382, 0.0174, 0.029, 0.04, 0.0198, 0.0192, 0.0196, 0.022, 0.0434, 0.125, 0.0234, 0.1061, 0.0248, 0.0328, 0.689, 0.0637, 0.0767, 0.0748, 0.0852, 0.1118, 0.0676, 0.0737, 0.4756, 0.0826, 0.0707, 0.0849, 0.0552, 0.0723, 0.0715, 0.0707, 0.0692, 0.0885, 0.0616, 0.0819, 0.0817, 0.0197, 0.037, 0.0213, 0.0321, 0.0303, 0.0257, 0.0253, 0.0272, 0.0399, 0.0354, 0.0272, 0.0409, 0.0265, 0.0565, 0.0632, 0.0351, 0.0539, 0.0285, 0.0203, 0.0385, 0.0276, 0.0291, 0.0482, 0.026, 0.0443, 0.0222, 0.1528, 0.1163, 0.0281, 0.0368, 0.0289, 0.0239, 0.2457, 0.1137, 0.0269, 0.0239, 0.0343, 0.0292, 0.0244, 0.0264, 0.096, 0.1331, 0.

In [ ]:
with open(csv_file_mon, mode='a', newline='') as file:
    writer = csv.writer(file)
    writer.writerow(avg_sum_intervals_continuous)
    writer.writerow(std_sum_intervals_continuous)
    writer.writerow(max_sum_intervals_continuous)

###time interval of incoming and outgoing packets

In [ ]:
sum_intervals_continuous=sum_interval(X1,X2)

outgoing_pkts_time_interval=[[] for i in range(19000)]
incoming_pkts_time_interval=[[] for i in range(19000)]

for i in range(19000):
  for j in range(len(sum_intervals_continuous[i])):
    if j%2==0:
      outgoing_pkts_time_interval[i].append(sum_intervals_continuous[i][j])
    else:
      incoming_pkts_time_interval[i].append(sum_intervals_continuous[i][j])

In [ ]:
avg_outgoing_pkts_time_interval = ['avg_outgoing_pkts_time_interval']
std_outgoing_pkts_time_interval = ['std_outgoing_pkts_time_interval']
# min_outgoing_pkts_time_interval = ['min_outgoing_pkts_time_interval']
max_outgoing_pkts_time_interval = ['max_outgoing_pkts_time_interval']

avg_incoming_pkts_time_interval = ['avg_incoming_pkts_time_interval']
std_incoming_pkts_time_interval = ['std_incoming_pkts_time_interval']
# min_incoming_pkts_time_interval = ['min_incoming_pkts_time_interval']
max_incoming_pkts_time_interval = ['max_incoming_pkts_time_interval']

for arr in outgoing_pkts_time_interval:
    # 각 1차원 배열의 평균, 표준편차, 최소값, 최대값 계산하여 배열에 추가
    avg_outgoing_pkts_time_interval.append(round(np.mean(arr),4))
    std_outgoing_pkts_time_interval.append(round(np.std(arr),4))
    # min_outgoing_pkts_time_interval.append(np.min(arr))
    max_outgoing_pkts_time_interval.append(np.max(arr))

for arr in incoming_pkts_time_interval:
    # 각 1차원 배열의 평균, 표준편차, 최소값, 최대값 계산하여 배열에 추가
    avg_incoming_pkts_time_interval.append(round(np.mean(arr),4))
    std_incoming_pkts_time_interval.append(round(np.std(arr),4))
    # min_incoming_pkts_time_interval.append(np.min(arr))
    max_incoming_pkts_time_interval.append(np.max(arr))

# 결과 확인
print(avg_outgoing_pkts_time_interval)
print(std_outgoing_pkts_time_interval)
# print(min_outgoing_pkts_time_interval)
print(max_outgoing_pkts_time_interval)


print(avg_incoming_pkts_time_interval)
print(std_incoming_pkts_time_interval)
# print(min_incoming_pkts_time_interval)
print(max_incoming_pkts_time_interval)

['avg_outgoing_pkts_time_interval', 0.0897, 0.0805, 0.0732, 0.0926, 0.1091, 0.0969, 0.1366, 0.0664, 0.15, 0.1342, 0.1112, 0.2588, 0.1867, 0.071, 0.0564, 0.0825, 0.1016, 0.091, 0.1283, 0.3144, 0.2109, 0.05, 0.0153, 0.0076, 0.0763, 0.093, 0.0171, 0.0364, 0.0199, 0.0165, 0.0072, 0.0169, 0.1674, 0.14, 0.0448, 0.055, 0.0161, 0.0609, 0.0177, 0.0175, 0.0186, 0.0421, 0.0282, 0.0172, 0.0184, 0.0392, 0.016, 0.0285, 0.0443, 0.0195, 0.0203, 0.0221, 0.023, 0.0475, 0.0293, 0.0258, 0.159, 0.0253, 0.0277, 1.2209, 0.0784, 0.0958, 0.0616, 0.0837, 0.1134, 0.0488, 0.0837, 0.4578, 0.063, 0.1005, 0.0761, 0.0514, 0.0547, 0.0522, 0.0441, 0.1018, 0.0797, 0.0869, 0.1077, 0.0937, 0.0229, 0.0405, 0.0196, 0.0233, 0.022, 0.0294, 0.0272, 0.0339, 0.0368, 0.0351, 0.0321, 0.0402, 0.0202, 0.0599, 0.0665, 0.0253, 0.0429, 0.0293, 0.0194, 0.03, 0.0291, 0.0218, 0.0459, 0.033, 0.044, 0.022, 0.157, 0.1097, 0.03, 0.0381, 0.0286, 0.0207, 0.2537, 0.2041, 0.0266, 0.0187, 0.0363, 0.0303, 0.0212, 0.0243, 0.1411, 0.0599, 0.274, 0.27

In [ ]:
with open(csv_file_mon, mode='a', newline='') as file:
    writer = csv.writer(file)
    writer.writerow(avg_outgoing_pkts_time_interval)
    writer.writerow(std_outgoing_pkts_time_interval)
    writer.writerow(max_outgoing_pkts_time_interval)
    writer.writerow(avg_incoming_pkts_time_interval)
    writer.writerow(std_incoming_pkts_time_interval)
    writer.writerow(max_incoming_pkts_time_interval)

###flow activity duration

In [ ]:
flow_act_duration=['flow_act_duration']

for i in range(19000):
  flow_act_duration.append(X1[i][-1])

print(flow_act_duration)

['flow_act_duration', 10.14, 10.16, 11.11, 13.36, 10.64, 10.74, 15.84, 8.85, 11.82, 12.35, 12.75, 12.25, 14.25, 10.67, 10.92, 11.74, 10.46, 10.65, 23.12, 28.77, 39.59, 52.26, 19.72, 18.45, 9.79, 10.92, 19.87, 9.98, 22.9, 19.67, 19.77, 15.97, 22.65, 20.23, 41.8, 56.51, 17.92, 9.97, 20.4, 55.9, 7.91, 17.74, 12.93, 7.13, 8.82, 17.73, 7.52, 11.79, 16.87, 8.52, 8.11, 8.84, 9.41, 17.98, 52.26, 10.5, 51.98, 11.41, 13.45, 63.39, 9.81, 11.2, 11.29, 11.84, 17.66, 9.93, 11.05, 57.07, 12.97, 10.89, 11.71, 10.98, 14.1, 11.22, 10.53, 13.15, 12.66, 9.11, 12.62, 11.6, 8.45, 15.52, 9.7, 13.07, 11.67, 13.95, 10.36, 11.22, 12.45, 9.83, 15.01, 17.51, 14.38, 23.94, 35.47, 19.34, 28.67, 11.51, 9.19, 21.67, 13.7, 14.42, 23.75, 12.56, 20.32, 11.15, 56.85, 54.21, 13.58, 17.98, 14.47, 11.55, 52.82, 55.16, 12.63, 11.71, 16.62, 13.59, 11.86, 12.7, 33.99, 37.79, 56.94, 22.34, 34.9, 35.79, 38.76, 33.12, 33.42, 56.55, 36.59, 32.63, 34.29, 33.82, 33.63, 33.57, 33.36, 33.89, 63.09, 71.11, 15.7, 10.31, 9.59, 11.89, 18.

In [ ]:
with open(csv_file_mon, mode='a', newline='') as file:
    writer = csv.writer(file)
    writer.writerow(flow_act_duration)

In [ ]:
csv_file_mon = '/content/drive/MyDrive/Colab Notebooks/2023_2_ML/mon.csv'

# CSV 파일 열기
with open(csv_file_mon, mode='r') as file:
    reader = csv.reader(file)
    for row in reader:
        first_element = row[0]  # 각 행의 첫 번째 원소
        print(first_element)

Label
total_pkt_per_user
total_outgoing_pkt_per_user
total_incoming_pkt_per_user
outgoing_pkt_frac_per_user
incoming_pkt_frac_per_user
outgoing30_per_user
incoming30_per_user
avg_total_burst_per_user
std_total_burst_per_user
max_total_burst_per_user
avg_incoming_burst_per_user
std_incoming_burst_per_user
min_incoming_burst_per_user
avg_outgoing_burst_per_user
std_outgoing_burst_per_user
max_outgoing_burst_per_user
avg_cumulative
std_cumulative
min_cumulative
avg_interval
std_interval
max_interval
avg_pkts_in_fixed_time
std_pkts_in_fixed_time
min_pkts_in_fixed_time
max_pkts_in_fixed_time
avg_sum_intervals_continuous
std_sum_intervals_continuous
max_sum_intervals_continuous
avg_outgoing_pkts_time_interval
std_outgoing_pkts_time_interval
max_outgoing_pkts_time_interval
avg_incoming_pkts_time_interval
std_incoming_pkts_time_interval
max_incoming_pkts_time_interval
flow_act_duration


In [23]:
csv_file_mon = '/content/drive/MyDrive/Colab Notebooks/2023_2_ML/mon.csv'
cnt = 0
# CSV 파일 열기
with open(csv_file_mon, mode='r') as file:

    reader = csv.reader(file)
    for row in reader:
        row_size = len(row)  # 각 행의 길이
        print(f"{cnt}행의 크기: {row_size}")
        cnt += 1

0행의 크기: 19001
1행의 크기: 19001
2행의 크기: 19001
3행의 크기: 19001
4행의 크기: 19001
5행의 크기: 19001
6행의 크기: 19001
7행의 크기: 19001
8행의 크기: 19001
9행의 크기: 19001
10행의 크기: 19001
11행의 크기: 19001
12행의 크기: 19001
13행의 크기: 19001
14행의 크기: 19001
15행의 크기: 19001
16행의 크기: 19001
17행의 크기: 19001
18행의 크기: 19001
19행의 크기: 19001
20행의 크기: 19001
21행의 크기: 19001
22행의 크기: 19001
23행의 크기: 19001
24행의 크기: 19001
25행의 크기: 19001
26행의 크기: 19001
27행의 크기: 19001
28행의 크기: 19001
29행의 크기: 19001
30행의 크기: 19001
31행의 크기: 19001
32행의 크기: 19001
33행의 크기: 19001
34행의 크기: 19001
35행의 크기: 19001
36행의 크기: 19001
